In [1]:
import pandas as pd
pd.set_option("display.max_columns", 500)
pd.set_option("display.max_rows", 500)

## Importamos los archivos

In [2]:
df_bajas = pd.read_feather('../../../data/processed/periodos_baja_x_cif_id.feather')

In [3]:
df_pagos = pd.read_feather('../../../data/processed/pagos_x_cif_id.feather')

In [4]:
df_interacciones = pd.read_feather('../../../data/processed/interacciones_tipo_periodo_x_cif_id.feather')

In [5]:
df_clientes = pd.read_feather('../../../data/interim/clientes.feather')

In [6]:
df_clientes = df_clientes.rename(columns={"ID":"CIF_ID"})

## Verificamos que todos se puedan combinar con la tabla Bajas

In [7]:
def check_merge(df1,df2,field):
    return len(set(df1[field].unique()).intersection(set(df2[field].unique()))) / len(df1[field].unique())

In [8]:
df_pagos.head()

CIF_ID  1_SITUACION_AM  1_SITUACION_CT  1_SITUACION_EP  2_SITUACION_AM  \
0   571.0             NaN             NaN             NaN             NaN   
1   573.0             NaN             1.0             NaN             NaN   
2  1009.0             NaN             NaN             NaN             NaN   
3  1103.0             NaN             3.0             NaN             NaN   
4  1313.0             NaN             1.0             NaN             NaN   

   2_SITUACION_CT  2_SITUACION_EP  3_SITUACION_AM  3_SITUACION_CT  \
0             NaN             NaN             NaN             1.0   
1             1.0             NaN             NaN             1.0   
2             1.0             NaN             NaN             1.0   
3             3.0             NaN             NaN             3.0   
4             1.0             NaN             NaN             1.0   

   3_SITUACION_EP  4_SITUACION_AM  4_SITUACION_CT  4_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             3.0             NaN   
4             NaN             NaN             1.0             NaN   

   4_SITUACION_PP  5_SITUACION_AM  5_SITUACION_CT  5_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             5.0             NaN   
4             NaN             NaN             1.0             NaN   

   5_SITUACION_PP  6_SITUACION_AM  6_SITUACION_CT  6_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             1.0             4.0   
4             NaN             NaN             1.0             NaN   

   6_SITUACION_PP  7_SITUACION_AM  7_SITUACION_CT  7_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             1.0             NaN   
4             NaN             NaN             1.0             NaN   

   7_SITUACION_PP  8_SITUACION_AM  8_SITUACION_CT  8_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             2.0             NaN   
4             NaN             NaN             1.0             NaN   

   8_SITUACION_PP  9_SITUACION_AM  9_SITUACION_CT  9_SITUACION_EP  \
0             NaN             NaN             1.0             NaN   
1             NaN             NaN             1.0             NaN   
2             NaN             NaN             1.0             NaN   
3             NaN             NaN             NaN             2.0   
4             NaN             NaN             1.0             NaN   

   9_SITUACION_PP  10_SITUACION_AM  10_SITUACION_CT  10_SITUACION_EP  \
0             NaN              NaN              1.0              NaN   
1             NaN              NaN              1.0              NaN   
2             NaN              NaN              1.0              NaN   
3             NaN              NaN              1.0              NaN   
4             NaN              NaN              1.0              NaN   

   10_SITUACION_PP  11_SITUACION_AM  11_SITUACION_CT  11_SITUACION_EP  \
0              NaN              NaN              1.0              NaN   
1              NaN              NaN              1.0    

In [9]:
check_merge(df_bajas, df_pagos, "CIF_ID")

0.9898176104661043

In [10]:
check_merge(df_bajas, df_clientes, "CIF_ID")

0.9880408313209732

In [11]:
df_clientes.isna().mean()

CIF_ID                           0.000000
ORIGEN                           0.000000
SEXO                             0.015428
TIPO_PERSONA                     0.000000
CLIENTE                          0.296385
ANO_DE_NACIMIENTO                0.060915
FECHA_NACIMIENTO                 0.074681
ESTADO_CIVIL                     0.197946
DATECO_TRABAJA                   0.672452
DATECO_AUTONOMO                  0.674803
DATECO_RAZON_SOCIAL_EMPLEADOR    0.898623
DATMAR_COMPLETO_ESTUDIOS         0.673591
DATMAR_NIVEL_EDUCACION           0.982548
POSICION_IVA                     0.342197
dtype: float64

**Note:** Hacer left join con esta tabla considerando que puede haber clientes sin interacciones

**Antes del merge: verificar registros sin pagos**

In [12]:
df_bajas[df_bajas["CIF_ID"].isin(list(set(df_bajas["CIF_ID"].unique()) - set(df_pagos["CIF_ID"].unique())))]

CIF_ID                         hist_polizas  periodo_baja
32          7821.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
137        38441.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
333        80753.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
392        89761.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
434        98746.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
449       100870.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
452       101301.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
671       125698.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
721       131351.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
934       152135.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
975       156340.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1179      196698.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1239      201215.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1244      203738.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1308      248141.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1522      297764.0  2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1576      301069.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
1719      312073.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
1766      320816.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
1869      356836.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2019      365932.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2158      373018.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2167      373629.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
2256      379992.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
2373      386262.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2379      386540.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2552      396375.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
2891      398701.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
2906      398781.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
2937      398999.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
3008      399448.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3014      399472.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3025      399556.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3175      400741.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
3211      400919.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3315      401710.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3454      402732.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3483      402936.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
3548      403489.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
3638      404189.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
3763      405215.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4057      407596.0  1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             5
4152      408327.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4279      409826.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4552      443824.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4573      445043.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4630      447077.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4710      447565.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
4976      450511.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
5341      477695.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
5375      477934.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
5426      478227.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
5502      478615.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4
5516      478684.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
5537      478816.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
5552      478937.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1            -1
5554      478957.0  1 

In [13]:
df_pagos[df_pagos["CIF_ID"].isin(list(set(df_pagos["CIF_ID"].unique()) - set(df_bajas["CIF_ID"].unique())))]

CIF_ID  1_SITUACION_AM  1_SITUACION_CT  1_SITUACION_EP  \
664       125785.0             NaN             1.0             NaN   
1034      162364.0             NaN             NaN             1.0   
1037      162714.0             NaN             1.0             NaN   
1103      188626.0             NaN             NaN             1.0   
1219      199783.0             NaN             1.0             NaN   
1455      283073.0             NaN             NaN             1.0   
1512      297417.0             NaN             NaN             1.0   
1762      328709.0             NaN             NaN             1.0   
1894      359800.0             NaN             1.0             NaN   
2088      370655.0             NaN             NaN             1.0   
2096      370859.0             NaN             NaN             1.0   
2211      378056.0             NaN             1.0             NaN   
2245      379993.0             NaN             1.0             NaN   
2428      389843.0             NaN             NaN             1.0   
2658      397230.0             NaN             NaN             1.0   
2904      398879.0             NaN             1.0             NaN   
3707      404968.0             NaN             1.0             NaN   
3872      406291.0             NaN             NaN             1.0   
4079      408006.0             NaN             NaN             1.0   
4081      408013.0             NaN             1.0             NaN   
4313      410701.0             NaN             NaN             1.0   
4503      442615.0             NaN             NaN             1.0   
4818      448270.0             NaN             1.0             NaN   
4841      448470.0             NaN             1.0             NaN   
5596      479463.0             NaN             NaN             1.0   
5700      485580.0             NaN             NaN             1.0   
5892      486900.0             NaN             NaN             1.0   
6063      504056.0             NaN             NaN             1.0   
6166      505763.0             NaN             1.0             NaN   
6584      531289.0             NaN             1.0             NaN   
7003      579605.0             NaN             1.0             NaN   
7103      580242.0             NaN             1.0             NaN   
7295      585314.0             NaN             1.0             NaN   
7337      585593.0             NaN             NaN             1.0   
7372      585893.0             NaN             1.0             NaN   
7659      588268.0             NaN             1.0             NaN   
7818      589659.0             NaN             NaN             1.0   
8064      638503.0             NaN             1.0             NaN   
8809      734189.0             NaN             1.0             NaN   
8926      737929.0             NaN             1.0             NaN   
9260      740403.0             NaN             1.0             NaN   
9484      748975.0             NaN             1.0             NaN   
9536      749541.0             NaN             1.0             NaN   
9649      750537.0             NaN             1.0             NaN   
9847      752148.0             NaN             NaN             1.0   
9915      752651.0             NaN             NaN             1.0   
10022     753452.0             NaN             NaN             NaN   
10666     759676.0             NaN             NaN             1.0   
10914     771075.0             NaN             1.0             NaN   
11039     776226.0             NaN             1.0             NaN   
11143     777267.0             NaN             1.0             NaN   
11253     778545.0             NaN             1.0             NaN   
11548     782459.0             NaN             1.0             NaN   
11682     784884.0             NaN             1.0             NaN   
11913     788196.0             NaN             1.0             NaN   
12059     790004.0             NaN             1.0             NaN   
12309     810654.0    

*Renombrando columnas de interacciones y descartando periodos que no vamos a analizar*

In [14]:
df_interacciones.columns

Index(['CIF_ID', '(1, 'A')', '(1, 'I')', '(1, 'O')', '(2, 'A')', '(2, 'I')',
       '(2, 'O')', '(3, 'A')', '(3, 'I')', '(3, 'O')', '(4, 'A')', '(4, 'I')',
       '(4, 'O')', '(5, 'A')', '(5, 'I')', '(5, 'O')', '(6, 'A')', '(6, 'I')',
       '(6, 'O')', '(7, 'A')', '(7, 'I')', '(7, 'O')', '(8, 'A')', '(8, 'I')',
       '(8, 'O')', '(9, 'A')', '(9, 'I')', '(9, 'O')', '(10, 'A')',
       '(10, 'I')', '(10, 'O')', '(11, 'A')', '(11, 'I')', '(11, 'O')',
       '(12, 'A')', '(12, 'I')', '(12, 'O')', '(13, 'A')', '(13, 'I')',
       '(13, 'O')', '(14, 'A')', '(14, 'I')', '(14, 'O')', '(15, 'A')',
       '(15, 'I')', '(15, 'O')', '(16, 'A')', '(16, 'I')', '(16, 'O')',
       '(17, 'A')', '(17, 'I')', '(17, 'O')', '(18, 'A')', '(18, 'I')',
       '(18, 'O')', '(19, 'A')', '(19, 'I')', '(19, 'O')', '(20, 'A')',
       '(20, 'I')', '(20, 'O')'],
      dtype='object')

In [15]:
df_interacciones = df_interacciones.rename(columns=lambda x: x.replace("(","").replace(")","").replace(", ","_TIPOINT_").replace("'","")) 

In [16]:
to_drop = [col for col in df_interacciones.drop('CIF_ID', axis=1).columns if int(col.split('_')[0])>18]

In [17]:
to_drop

['19_TIPOINT_A',
 '19_TIPOINT_I',
 '19_TIPOINT_O',
 '20_TIPOINT_A',
 '20_TIPOINT_I',
 '20_TIPOINT_O']

In [18]:
df_interacciones.drop(to_drop, axis=1, inplace=True)

In [19]:
check_merge(df_bajas, df_interacciones, "CIF_ID")

0.9928603193114319

## Merge entre tablas

In [20]:
len(df_bajas)

982677

In [21]:
len(df_interacciones)

1872729

In [22]:
len(df_pagos)

979749

In [23]:
len(df_clientes)

11650636

In [24]:
df_bajas_int =  pd.merge(df_bajas, df_interacciones, on=['CIF_ID'], how='left')

In [25]:
df_bajas_int

CIF_ID                         hist_polizas  periodo_baja  \
0            571.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
1            573.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
2           1009.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
3           1103.0  3 3 3 3 3 1 1 1 0 1 1 1 1 1 1 1 1 1            -1   
4           1313.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
5           1429.0  2 2 2 2 2 2 2 2 2 2 2 2 2 0 0 0 0 0            16   
6           1482.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
7           1559.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
8           1774.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
9           1779.0  0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1            -1   
10          1923.0  1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             6   
11          2643.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
12          2994.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
13          3454.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
14          4408.0  1 1 1 1 1 1 1 1 1 2 1 1 1 1 1 1 1 1            -1   
15          4431.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
16          4598.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
17          4655.0  3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3            -1   
18          4673.0  1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             6   
19          5049.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0            18   
20          5067.0  0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1            -1   
21          5096.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
22          5231.0  1 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2            -1   
23          5332.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
24          5575.0  1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0            10   
25          5915.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
26          5937.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
27          6333.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
28          6584.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
29          6964.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1            -1   
30          7757.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
31          7759.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
32          7821.0  1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0             4   
33          7870.0  2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2            -1   
34          7968.0  2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2            -1   
35          8091.0  0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1            -1   
36          8144.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1            -1   
37          8164.0  1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0            13   
38          8286.0  2 2 2 2 2 2 2 1 1 2 1 1 1 1 1 1 1 1            -1   
39          8495.0  1 1 1 1 1 1 1 1 1 1 1 1 1 2 2 1 1 1            -1   
40          8904.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0            18   
41          8974.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
42          9028.0  2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2 2            -1   
43          9114.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
44          9226.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
45          9831.0  1 1 1 1 1 1 1 2 1 1 1 1 1 1 1 1 1 1            -1   
46          9843.0  1 1 1 1 1 1 1 1 2 1 1 1 1 1 1 1 1 1            -1   
47         10007.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
48         10833.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
49         11169.0  0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1            -1   
50         11684.0  0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1            -1   
51         11706.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
52         11818.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1   
53         11820.0  1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1            -1 

In [26]:
from functools import reduce
df_merged = reduce(lambda  left,right: pd.merge(left, right, on=['CIF_ID'], how='inner'), [df_bajas_int, df_pagos, df_clientes])

In [27]:
df_merged.shape

(961000, 265)

### Guardamos la tabla completa

In [28]:
df_merged.to_feather('../../../data/processed/merged_data_18_periods.feather')

--- 

In [1]:
import pandas as pd
df_merged = pd.read_feather('../../../data/processed/merged_data_18_periods.feather')

In [2]:
"], [".join(set([''.join([s for s in col if not s.isdigit()]) for col in df_merged.columns]))

'_COBRO_TA], [hist_polizas], [_COBRO_PP], [_TIPOINT_A], [SEXO], [_COBRO_CC], [ANO_DE_NACIMIENTO], [ORIGEN], [_COBRO_SJ], [DATECO_RAZON_SOCIAL_EMPLEADOR], [_COBRO_BA], [CLIENTE], [_SITUACION_PP], [ESTADO_CIVIL], [_TIPOINT_I], [_SITUACION_AM], [MONTO_PAGO_], [DATECO_TRABAJA], [DATMAR_NIVEL_EDUCACION], [demora_pago_], [DATMAR_COMPLETO_ESTUDIOS], [FECHA_NACIMIENTO], [POSICION_IVA], [_SITUACION_EP], [periodo_baja], [TIPO_PERSONA], [DATECO_AUTONOMO], [_TIPOINT_O], [CIF_ID], [_SITUACION_CT'